# Introduction

This colab notebook shows how to extract a large Google Open Buildings dataset and gecode it into a human-readable address. The final product is the dataframe that can be used for further analysis.

# Setup

In [ ]:
!pip install ee
!pip install earthengine-api --upgrade
!pip install openpyxl
!pip install folium
!pip install geopandas
!pip install matplotlib
!pip install tqdm

In [15]:
import geopandas as gpd
import pandas as pd
import matplotlib as plt
import requests
import time
import random
import gzip
from tqdm import tqdm

# Data

This notebook explores the Open Building Footprint datasets in hopes of geocoding building attributes for various countries.

In particular, the codes below works for the Indonesia datasets that can be found at the shared volunteer Google Drive, or downloaded directly from the Google Open Buildings at: https://sites.research.google/open-buildings/

### Mounting personal Google Drive for data access

In [12]:
#Mount the Google Drive
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [4]:
all_files = [['/content/gdrive/MyDrive/DataDive/indonesia1.csv.gz',
              '/content/gdrive/MyDrive/DataDive/indonesia2.csv.gz',
              '/content/gdrive/MyDrive/DataDive/indonesia3.csv.gz',
              '/content/gdrive/MyDrive/DataDive/indonesia4.csv.gz']]

### Sampling the datasets

The python module, "csv_gz_sampler.py", efficiently reads large gzipped CSV files and offers random sampling of the datasets. Using it, we will read 5,000 random rows for each Indonesia dataset and save them as a dataframe.

In [55]:
#Use csv_gz_sampler.py below to read 5000 random rows
def sample_rows_from_csv_gz(filename: str, n: int = 10000) -> pd.DataFrame:
    """
    Randomly sample n rows from a gzipped CSV file.

    Parameters:
    - filename (str): Path to the gzipped CSV file.
    - n (int): Number of rows to sample. Default is 10,000.

    Returns:
    - pd.DataFrame: A dataframe containing the sampled rows.
    """

    # Determine the total number of rows in the file
    with gzip.open(filename, "rt") as f:
        total_rows = sum(1 for row in tqdm(f, desc="Counting rows"))

    # If there are fewer than n rows, return all rows
    if total_rows <= n:
        return pd.read_csv(filename, compression='gzip')

    # Calculate the number of rows to skip
    skip_rows = total_rows - n
    # Randomly select rows to skip
    skipped_rows = random.sample(range(1, total_rows), skip_rows)

    # Read the CSV file with progress updates and concatenate the chunks
    chunks = pd.read_csv(filename, compression='gzip', skiprows=skipped_rows, iterator=True, chunksize=1000)
    df = pd.concat(tqdm(chunks, total=n//1000, desc="Loading data"), ignore_index=True)

    return df

if __name__ == "__main__":
    # declare dataframe
    df = pd.DataFrame()
    # get list of files from the local files
    all_files = ['/content/gdrive/MyDrive/DataDive/indonesia1.csv.gz',
                 '/content/gdrive/MyDrive/DataDive/indonesia2.csv.gz',
                 '/content/gdrive/MyDrive/DataDive/indonesia3.csv.gz',
                 '/content/gdrive/MyDrive/DataDive/indonesia4.csv.gz']
    # iterate through the files and append to current dataframe
    for file in all_files:
      df = df.append(sample_rows_from_csv_gz(file, 5000))
    print(df)

Counting rows: 4264386it [01:02, 68547.91it/s]
Loading data: 100%|██████████| 5/5 [00:18<00:00,  3.78s/it]
<ipython-input-55-c053192bf0bf>:43: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(sample_rows_from_csv_gz(file, 5000))
Counting rows: 4111980it [01:05, 63240.14it/s]
Loading data: 100%|██████████| 5/5 [00:20<00:00,  4.15s/it]
<ipython-input-55-c053192bf0bf>:43: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(sample_rows_from_csv_gz(file, 5000))
Counting rows: 1215566it [00:23, 52339.95it/s]
Loading data: 100%|██████████| 5/5 [00:04<00:00,  1.04it/s]
<ipython-input-55-c053192bf0bf>:43: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(sample_rows_from_csv_gz(file, 5000))
Counting r

      latitude   longitude  area_in_meters  confidence  \
0    -1.245557  116.915888         28.4829      0.7436   
1    -0.577809  117.015944         24.6598      0.8234   
2    -1.519726  116.322718         10.4901      0.6686   
3    -3.449102  114.714665         44.9024      0.7658   
4    -2.617285  114.666420          8.7079      0.7519   
...        ...         ...             ...         ...   
4994 -1.170208  112.497110         49.8371      0.7301   
4995 -2.036648  110.123207         75.5033      0.8039   
4996 -1.276943  111.679113         37.2373      0.8096   
4997 -2.993738  112.330675        305.1049      0.6522   
4998 -0.149746  109.405668        116.6392      0.8146   

                                               geometry full_plus_code  
0     POLYGON((116.915910637434 -1.24558182166721, 1...  6PCRQW38+Q9CM  
1     POLYGON((117.015973524143 -0.577798377468137, ...  6PFVC2C8+V9GJ  
2     POLYGON((116.322728454398 -1.51974428401151, 1...  6PCRF8JF+434X  
3     POLYG


<ipython-input-55-c053192bf0bf>:43: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(sample_rows_from_csv_gz(file, 5000))


In [58]:
print(df.head())

   latitude   longitude  area_in_meters  confidence  \
0 -1.245557  116.915888         28.4829      0.7436   
1 -0.577809  117.015944         24.6598      0.8234   
2 -1.519726  116.322718         10.4901      0.6686   
3 -3.449102  114.714665         44.9024      0.7658   
4 -2.617285  114.666420          8.7079      0.7519   

                                            geometry full_plus_code  
0  POLYGON((116.915910637434 -1.24558182166721, 1...  6PCRQW38+Q9CM  
1  POLYGON((117.015973524143 -0.577798377468137, ...  6PFVC2C8+V9GJ  
2  POLYGON((116.322728454398 -1.51974428401151, 1...  6PCRF8JF+434X  
3  POLYGON((114.714713760428 -3.4490893575055, 11...  6P8PHP27+9V3V  
4  POLYGON((114.66643096435 -2.61730061169831, 11...  6P9P9MM8+3HMM  


# Reverse Geocoding

Reverse geocoding using Nominatim API has been done below. It converts geographic coordinates into a human-readable address. The end-results are stored into a dataframe, df.

In [23]:
import requests
import time

In [78]:
chosen_country = 'Indonesia' #Can be adjusted
#Filter data to include confidence level of 85% or above; number is adjustable
df_highconf = df[df['confidence'] >= 0.85]

# Define a function to get an address from given latitude and longitude using the Nominatim API.
def get_address_from_coords(lat, lon):
    # Base URL for the Nominatim reverse geocoding API
    base_url = "https://nominatim.openstreetmap.org/reverse"
    # Parameters to be passed with the API request
    params = {
        "format": "json",
        "lat": lat,
        "lon": lon
    }
    try:
        response = requests.get(base_url, params=params, timeout=10)
        response.raise_for_status()
        data = response.json() # Parse the JSON response to get the address data
        return data
    except requests.RequestException as e:
        # Handle any exceptions related to the request, such as timeouts, connectivity issues, etc.
        print(f"Error fetching data for lat={lat}, lon={lon}. Error: {e}")
        return None

# Entry point for the script execution
if __name__ == "__main__":
    # Display the number of buildings that we are going to fetch data for
    print(f"Finding administrative divisions for {len(df_highconf)} buildings \n\n")

    # Loop through each building in the dataframe
    for index, row in df_highconf.iterrows():
        # Fetch the human-readable address for the given coordinates of the building
        address = get_address_from_coords(row.latitude, row.longitude)

        # If an address is found and it is located in the chosen country, update the dataframe with the relevant details
        if address and address.get('address', {}).get('country') == chosen_country:
            df_highconf.at[index, 'Country'] = address['address'].get('country', '')
            df_highconf.at[index, 'Province'] = address['address'].get('province', '')
            df_highconf.at[index, 'County'] = address['address'].get('county', '')
            df_highconf.at[index, 'Country_code'] = address['address'].get('country_code', '')
            df_highconf.at[index, 'State'] = address['address'].get('state', '')
            df_highconf.at[index, 'ISO3166-2-lvl4'] = address['address'].get('ISO3166-2-lvl4', '')
            df_highconf.at[index, 'Type'] = address.get('type', '')
            df_highconf.at[index, 'Class'] = address.get('class', '')


        # Print progress for each row to track the process
        print(f"Row <------> {index+1} written <------> {address}")
        2
        # Pause for 1 second (Nominatim's usage policy)
        time.sleep(1)

Finding administrative divisions for 4987 buildings 


Row <------> 7 written <------> {'place_id': 56086403, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'way', 'osm_id': 632079622, 'lat': '-2.541337834146552', 'lon': '112.94828261393432', 'class': 'highway', 'type': 'tertiary', 'place_rank': 26, 'importance': 0.10000999999999993, 'addresstype': 'road', 'name': 'M.T. Haryono', 'display_name': 'M.T. Haryono, Sampit, Kotawaringin Timur, Kalimantan Tengah, Kalimantan, 74322, Indonesia', 'address': {'road': 'M.T. Haryono', 'town': 'Sampit', 'county': 'Kotawaringin Timur', 'state': 'Kalimantan Tengah', 'ISO3166-2-lvl4': 'ID-KT', 'region': 'Kalimantan', 'ISO3166-2-lvl3': 'ID-KA', 'postcode': '74322', 'country': 'Indonesia', 'country_code': 'id'}, 'boundingbox': ['-2.5413566', '-2.5411697', '112.9419363', '112.9494251']}
Row <------> 22 written <------> {'place_id': 56079295, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://os

In [82]:
df_highconf.head()

latitude   longitude  area_in_meters  confidence  \
6  -2.541446  112.948286         47.3045      0.8964   
21 -3.287871  114.608558         73.2195      0.8512   
25 -3.800744  115.231198        383.7601      0.9284   
28 -0.613051  114.570504         54.0723      0.8947   
35 -3.506823  114.522807        106.5499      0.9142   

                                             geometry full_plus_code  \
6   POLYGON((112.948331069698 -2.54146569569892, 1...  6P9JFW5X+C8F2   
21  POLYGON((114.608590306404 -3.28791795354949, 1...  6P8PPJ65+VC35   
25  POLYGON((115.231285028105 -3.80081187506898, 1...  6P8Q56XJ+PF47   
28  POLYGON((114.570547685329 -0.613031402273867, ...  6PFP9HPC+Q6CR   
35  POLYGON((114.522834621874 -3.5068905654938, 11...  6P8PFGVF+74F5   

      Country Province              County Country_code               State  \
6   Indonesia           Kotawaringin Timur           id   Kalimantan Tengah   
21  Indonesia                     Ketapang           id    Kalimantan Barat   
25  Indonesia                                        id    Sulawesi Selatan   
28  Indonesia                  Murung Raya           id   Kalimantan Tengah   
35  Indonesia                       Banjar           id  Kalimantan Selatan   

   ISO3166-2-lvl4          Type    Class  
6           ID-KT      tertiary  highway  
21          ID-KB   residential  highway  
25          ID-SN  unclassified  highway  
28          ID-KT   residential  highway  
35          ID-KS   residential  highway

### Exporting high confidence dataframe

In [83]:
df_highconf.to_csv('indonesia_geocoded.csv', index=False)

# Visualization

### Converting to geodataframe

In [84]:
# convert to geodataframe
gdf = df_highconf.GeoDataFrame(df)

gdf['geometry'] = gpd.GeoSeries.from_wkt(gdf['geometry'])

# Now set the active geometry column to the column named 'geometry'
gdf = df_highconf.set_geometry('geometry')


# # Set the initial crs to epsg:4326 then reproject to epsg:3857 for plotting
# sample_data = sample_data.set_crs(epsg=4326)
# sample_data = sample_data.to_crs(epsg=3857)

# print(sample_data.crs)

# sample_data['geometry'].is_valid.value_counts()

AttributeError: ignored

### Interactive plot using Folium

In [38]:
# Interactive plot using Folium

import folium
from folium.plugins import FeatureGroupSubGroup
import matplotlib.pyplot as plt
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.colors as mcolors
from folium import plugins
from folium.plugins import FloatImage
from shapely import wkt
import base64
import os


# initialise map
m = folium.Map(zoom_start=2)

# # Create main feature group
# main_fg = folium.FeatureGroup(name='Main Group')
# m.add_child(main_fg)

# # # Loop through each file in the list
# # for file in all_files:
#     # Read the file as a DataFrame
# df = pd.read_csv('indonesia1.csv')

#   # Convert the 'geometry' column from strings to geometry objects
# df['geometry'] = df['geometry'].apply(wkt.loads)

#   # Convert the DataFrame to a GeoDataFrame
# gdf = gpd.GeoDataFrame(df, geometry='geometry')

df_highconf = pd.read.csv('indonesia.csv')
  # # Set the initial crs to epsg:4326 then reproject to epsg:3857 for plotting with Folium
gdf = gdf.set_crs(epsg=4326)
gdf = gdf.to_crs(epsg=3857)


print('Valid geometry query: ', gdf['geometry'].is_valid.value_counts())

  # Get unique values from a column (adjust column name as needed)
unique_types = gdf['ISO3166-2-lvl4'].unique()

  # Generate a list of distinct colors
colors = plt.cm.tab10(np.linspace(0, 1, len(unique_types)))

  # Convert the RGBA colors to hexadecimal format
hex_colors = [mcolors.rgb2hex(color) for color in colors]

  # Create a dictionary mapping each unique type to a color
type_color_mapping = dict(zip(unique_types, hex_colors))

  # Add the polygons from the GeoDataFrame to the map
geojson_layer = folium.GeoJson(
      gdf,
      style_function=lambda feature: {
          'fillColor': '#f79122', # DataKind orange
          'color': type_color_mapping.get(feature['properties']['ISO3166-2-lvl4'], '#f79122'),  # Adjust the colour attribute here
          'weight': 3.5,
          'fillOpacity': 0.3,
        },
      tooltip=folium.GeoJsonTooltip(
          fields=["Country", "Province", "County", "State", "ISO3166-2-lvl4", "Type"],
          aliases=["Country:", "Province:", "County:", "State:", "ISO:", "Type:"],
          localize=False
      ),
      highlight_function=lambda x: {'weight': 2.5, 'color': 'cyan'}
  )
geojson_layer.add_to(main_fg)

# Add a tile layer to the map (in this case, a satellite view from OpenStreetMap)
tile_layer = folium.TileLayer(
    tiles="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}",
    attr="Esri",
    name="Esri Satellite"
)
tile_layer.add_to(m)

# Add a layer control to switch between different layers
folium.LayerControl().add_to(m)


################### wigits and plugins ###################

# Minimap
minimap = plugins.MiniMap(position = 'bottomleft', toggle_display = True)
m.add_child(minimap)

# Save the map
m.save('Geocoding_validation_map.html')

# Display the map
m

Valid geometry query:  True    1144
dtype: int64
